In [4]:
import os
import cv2
import json
import copy
import random
import argparse


def get_args(argv=None):
    """ Prepare auguments for running the script """

    parser = argparse.ArgumentParser(
        description='via to yolo format'
    )
    parser.add_argument(
        '-i',
        '--input',
        type=str,
        default='',
        help='Input via json file.')
    parser.add_argument(
        '-f',
        '--img_folder',
        type=str,
        default='',
        help='Image folder.')
    parser.add_argument(
        '-o',
        '--output_folder',
        type=str,
        default='',
        help='Output folder')
    parser.add_argument(
        '--lr_flip', dest='lr_flip',
        action='store_true', default=False,
        help='True to augment data by left-right flip.'
    )
    parser.add_argument(
        '-r',
        '--split_ratio',
        type=float,
        default=0.8,
        help='Split ratio of training data.')
    return parser.parse_args(argv)

# parse arguments
args = get_args()
cwd = os.getcwd()
json_fn = os.path.join(cwd, 'via_export_json.json')
img_folder = os.path.join(cwd, 'data')
out_folder = os.path.join(cwd, 'out')

# read in json data
with open(json_fn) as data_file:
    data = json.load(data_file)

# create output folder
if not os.path.exists(out_folder):
    os.makedirs(out_folder)

# record labels for obj.names
labels = []

# record image filenames for train.txt and test.txt
img_fns = []

# loop over labeled images
for idx in data.keys():

    # read in image to get image width and height
    fn_img = os.path.join(img_folder, data[idx]['filename'])
    img = cv2.imread(fn_img)
    im_h, im_w = img.shape[:2]
    
    # record image filenames
    img_fns.append(fn_img)

    # create txt file with the same filename as the image file
    fn_txt = os.path.join(img_folder,
                          data[idx]['filename'].split('.')[0] + '.txt')
    fp_txt = open(fn_txt, 'w')
    print('Write label file:', fn_txt)

    # data augmentation: left-right flip
    if args.lr_flip:

        # write flipped image
        img_flip = cv2.flip(img, 1)
        fn_img_flip = os.path.join(
            args.img_folder,
            data[idx]['filename'].split('.')[0] +
            '_flip.jpg')
        cv2.imwrite(fn_img_flip, img_flip)

        # record flip image filenames
        img_fns.append(fn_img_flip)

        # create txt file for flipped image
        fn_txt_flip = os.path.join(
            img_folder,
            data[idx]['filename'].split('.')[0] +
            '_flip.txt')
        fp_txt_flip = open(fn_txt_flip, 'w')

    # loop over labeled objects
    for obj in data[idx]['regions']:

        # extract label, x, y, width, height
        label = obj['region_attributes']['type']
        x = obj['shape_attributes']['x']
        y = obj['shape_attributes']['y']
        w = obj['shape_attributes']['width']
        h = obj['shape_attributes']['height']

        # register new label
        if label not in labels:
            labels.append(label)

        # get label id
        label_id = labels.index(label)

        # write obj information
        fp_txt.writelines('{} {} {} {} {}\n'.format(
            str(label_id),
            str((x + w / 2) / im_w),
            str((y + h / 2) / im_h),
            str(w / im_w),
            str(h / im_h)))

        # write obj information in fliped image
        if args.lr_flip:
            fp_txt_flip.writelines('{} {} {} {} {}\n'.format(
                str(label_id),
                str(1 - (x + w / 2) / im_w),
                str((y + h / 2) / im_h),
                str(w / im_w),
                str(h / im_h)))

    # close txt file
    fp_txt.close()
    if args.lr_flip:
        fp_txt_flip.close()

# create obj.names
fn_names = os.path.join(out_folder, 'obj.names')
fp_names = open(fn_names, 'w')
for label in labels:
    fp_names.writelines(label + '\n')
print('Write file: ', fn_names)
fp_names.close()

# shuffle image fn list
random.shuffle(img_fns, random.random)

# get split number
num = int(args.split_ratio * len(img_fns))

# create train.txt
fn_train = os.path.join(out_folder, 'train.txt')
fp_train = open(fn_train, 'w')
for fi in range(num):
    fp_train.writelines(img_fns[fi] + '\n')
print('Write file: ', fn_train)
fp_train.close()

# create test.txt
fn_test = os.path.join(out_folder, 'test.txt')
fp_test = open(fn_test, 'w')
for fi in range(num, len(img_fns)):
    fp_test.writelines(img_fns[fi] + '\n')
print('Write file: ', fn_test)
fp_test.close()

# create obj.data
fn_data = os.path.join(out_folder, 'obj.data')
fp_data = open(fn_data, 'w')
data = 'classes= {}\ntrain  = {}\nvalid  = {}\nnames = {}\nbackup = {}\n'.format(
    str(len(labels)),
    fn_train,
    fn_test,
    fn_names,
    os.path.join(out_folder, 'backup')
)
fp_data.writelines(data)
print('Write file: ', fn_data)
fp_data.close()


Write label file: C:\Users\User\Untitled Folder 1\data\00000001.txt
Write label file: C:\Users\User\Untitled Folder 1\data\00000003.txt
Write label file: C:\Users\User\Untitled Folder 1\data\00000004.txt
Write label file: C:\Users\User\Untitled Folder 1\data\00000005.txt
Write label file: C:\Users\User\Untitled Folder 1\data\00000006.txt
Write label file: C:\Users\User\Untitled Folder 1\data\00000009.txt
Write label file: C:\Users\User\Untitled Folder 1\data\00000066.txt
Write label file: C:\Users\User\Untitled Folder 1\data\00000069.txt
Write file:  C:\Users\User\Untitled Folder 1\out\obj.names
Write file:  C:\Users\User\Untitled Folder 1\out\train.txt
Write file:  C:\Users\User\Untitled Folder 1\out\test.txt
Write file:  C:\Users\User\Untitled Folder 1\out\obj.data
